In [1]:
#imports
import pandas as pd
%matplotlib inline 
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()
import calendar
import folium
from folium import plugins
from folium.plugins import HeatMap
import ipywidgets
import geocoder
import geopy

In [2]:
df_customers = pd.read_excel('Customers.xlsx', index_col="CustomerID")

## Data Preprocessing

In [3]:
df_customers.shape

(2272, 31)

In [4]:
df_customers.count()

First Name        2272
Last Name         2272
Address           2272
City              2272
State             2271
Postal Code       2271
Work Phone         915
Home Phone        2243
AccountBalance    2272
OpenedDate        2272
ActivityDate      2272
StoreID           2272
ActiveInd         2272
CheckFee          2272
Date1                0
Text1                0
Num1              2272
ConsignCode          0
Street2            151
Return            2272
ActiveItems        465
CustNotes         2243
Email             2193
CheckAmt          2039
PickupDate         708
BirthMonth           2
PickupDate2        171
PickupDate3         73
UseMRW            2272
TotalSales        2272
Locked            2272
dtype: int64

In [5]:
df_customers.dtypes

First Name                object
Last Name                 object
Address                   object
City                      object
State                     object
Postal Code              float64
Work Phone               float64
Home Phone               float64
AccountBalance           float64
OpenedDate                object
ActivityDate              object
StoreID                    int64
ActiveInd                   bool
CheckFee                   int64
Date1                    float64
Text1                    float64
Num1                       int64
ConsignCode              float64
Street2                   object
Return                      bool
ActiveItems              float64
CustNotes                 object
Email                     object
CheckAmt                 float64
PickupDate        datetime64[ns]
BirthMonth               float64
PickupDate2       datetime64[ns]
PickupDate3       datetime64[ns]
UseMRW                      bool
TotalSales               float64
Locked    

In [6]:
df_customers['StoreID'].unique()
# will drop from dataframe

array([1])

In [7]:
df_customers['ActiveInd'].value_counts()

True     2269
False       3
Name: ActiveInd, dtype: int64

In [8]:
df_customers['CheckFee'].value_counts()
# will drop

0       2166
9999     106
Name: CheckFee, dtype: int64

In [9]:
df_customers['Num1'].value_counts()
# will drop

50    2270
0        2
Name: Num1, dtype: int64

In [10]:
df_customers['Street2'].unique()

array([nan, 'Unit 3', '#141', 'STE 18-137', 'Apt 2607', '#2209', '#418',
       'Edmond', 'Ste. 505', '#1', 'A204', '#118', '#6311', '#103',
       'Apt K', 'Apt. 924', 'Apt. C', 'Apt. A', 'Villa 82', 'Apt. 1138',
       'Apt #1138', 'Apt 425', 'Apt 204', 'Apt 104', 'Unit 61', '207B',
       '#A120', '#112', '#2222', '#G', '#18201', 'Apt. 452', 'Apt 8210',
       'Apt. 14k1', 'Apt 2320', 'Apt. 612', 'Oak Hollow Rd', 'Apt. 132',
       '#24101', '#909', 'Unit 101', '#803', '#340', 'Ste. 200',
       'Apt 248', '#9', 'Apt. 17D', 'Apt 16108', 'Apt 1005', 'Apt 1512',
       '#225A', 'Unit #185', '#22', '#309', 'Apt # 1702', '9-137',
       'Suite #1550', 'Apt 1428', 'Suite 1403', 'Villa 80', 'Apt #4',
       'Apt 418', 'Dale St', '#2117', 'Apt. 19208', '910 S. Main',
       '#2705', 'Suite 112', '#276', 'Unit 150', 'Apt # 155', '#14',
       '#465', 'Apt 5108', 'Apt 222', '#233', 'Villa 27', 'Apt 134',
       'Suite 200', '#169', 'Unit B', '#201', 'Suite 3121', 'Apt 202',
       '#31', 'AP

In [11]:
df_customers['ActiveItems'].unique()

array([ 0., 44.,  1., 14.,  3.,  2.,  7.,  4., 19.,  6., 76., 11., 57.,
        5., 94., 16.,  8., 17., 12.,  9., 25., 41., nan])

In [12]:
df_customers['CustNotes'].unique()

array([nan, 'Store', 'Owes $50 p/u 9-17-15 njl', ...,
       'PU $75 GG 8/12/2020', 'Brought in 8/12/2020 GG', 'Brout in'],
      dtype=object)

In [13]:
df_customers['CheckAmt'].value_counts()
# will drop

0.0    2039
Name: CheckAmt, dtype: int64

In [14]:
df_customers['Locked'].value_counts()
# will drop

False    2272
Name: Locked, dtype: int64

In [15]:
# deleting columns that will not be relevant to this analysis
# including first and last names to maintain privacy
df_customers = df_customers.drop(['First Name','Last Name','Work Phone','Home Phone','Date1', 'Text1','ConsignCode','BirthMonth','StoreID','CheckFee',
                                  'Num1','Email','ActiveInd','Return','CustNotes','CheckAmt','UseMRW','Locked'], axis=1)
# drop the first row which is just a filler row
df_customers = df_customers.drop([0])
df_customers.head()

Address           City State  Postal Code  \
CustomerID                                                            
1                 3704 N. Western  Oklahoma City    OK      73118.0   
2           1503 Winding Ridge Rd         Edmond    OK      73034.0   
3                8309 NW 146th St  Oklahoma City    OK      73142.0   
4                 3802 US HWY 377            Ada    OK      74820.0   
5                702 Wakefield Rd          Perry    OK      73077.0   

            AccountBalance OpenedDate ActivityDate Street2  ActiveItems  \
CustomerID                                                                
1                   118.24  9/18/2015    8/12/2020     NaN          0.0   
2                     0.00  9/18/2015     4/5/2016     NaN          0.0   
3                     5.00  9/22/2015     7/2/2017     NaN          0.0   
4                     1.88  9/23/2015    5/22/2018     NaN          0.0   
5                     0.00  9/23/2015    6/29/2020     NaN          0.0   

           PickupDate PickupDate2 PickupDate3  TotalSales  
CustomerID                                                 
1          2015-07-20  2016-06-05  2019-04-26  768531.800  
2          2015-12-17         NaT         NaT     249.500  
3          2015-12-21         NaT         NaT    1501.191  
4          2015-12-22         NaT         NaT    9924.199  
5                 NaT         NaT         NaT    1533.500

In [16]:
# change 'Postal Code' from a float to a string
df_customers['Postal Code'] = df_customers['Postal Code'].astype(str).str[:-2]

# check that column is of dtype Object ('O')
df_customers['Postal Code'].dtypes

dtype('O')

In [17]:
# convert column datatypes to proper datetime formats
df_customers['OpenedDate'] = pd.to_datetime(df_customers['OpenedDate'], format='%d:%m:%Y', infer_datetime_format=True)
df_customers['ActivityDate'] = pd.to_datetime(df_customers['ActivityDate'], format='%d:%m:%Y', infer_datetime_format=True)
print(df_customers['OpenedDate'].dtype)
print(df_customers['ActivityDate'].dtype)

datetime64[ns]
datetime64[ns]


In [18]:
# Round Total Sales column to 2 decimal places to properly represent dollar amounts
df_customers['TotalSales'] = df_customers['TotalSales'].round(2)
df_customers.head(3)

Address           City State Postal Code  \
CustomerID                                                           
1                 3704 N. Western  Oklahoma City    OK       73118   
2           1503 Winding Ridge Rd         Edmond    OK       73034   
3                8309 NW 146th St  Oklahoma City    OK       73142   

            AccountBalance OpenedDate ActivityDate Street2  ActiveItems  \
CustomerID                                                                
1                   118.24 2015-09-18   2020-08-12     NaN          0.0   
2                     0.00 2015-09-18   2016-04-05     NaN          0.0   
3                     5.00 2015-09-22   2017-07-02     NaN          0.0   

           PickupDate PickupDate2 PickupDate3  TotalSales  
CustomerID                                                 
1          2015-07-20  2016-06-05  2019-04-26   768531.80  
2          2015-12-17         NaT         NaT      249.50  
3          2015-12-21         NaT         NaT     1501.19

In [19]:
df_customers.shape

(2271, 13)

# Analysis: Where do customers come from?
## Look at
### - Map all customers
### - Bin by total sales and view highest paying customers
### - Identify recurring customers and locations
### - Identify customer areas in relation to competitors

In [20]:
# Display top 10 area codes customers come from
df_customers['Postal Code'].value_counts().head(10)

73120    205
73013    198
73118    179
73012    141
73116    119
73034    101
73112     86
73142     85
73162     74
73099     71
Name: Postal Code, dtype: int64

In [21]:
df_customers.isnull()['Address'].value_counts()

False    2271
Name: Address, dtype: int64

In [22]:
df_customers.isnull()['City'].value_counts()

False    2271
Name: City, dtype: int64

In [23]:
df_customers.isnull()['State'].value_counts()

False    2271
Name: State, dtype: int64

In [24]:
df_customers.isnull()['Postal Code'].value_counts()

False    2271
Name: Postal Code, dtype: int64

In [25]:
df_customers['Full Address'] = df_customers['Address'] + ", " + df_customers['City'] + ", " + df_customers['State'] + " " + df_customers['Postal Code']

In [26]:
address_list = df_customers[['Full Address']]

# export to csv to input to online reverse geocoder to obtain coordinates to merge
# address_list.to_csv('addresses.csv', header=True)

In [27]:
# Import new csv file containing proper coordinates ran through geocoder
missing_addresses = pd.read_csv('missing_addresses.csv', index_col='CustomerID')
missing_addresses.head(3)

Full Address   Latitude  Longitude
CustomerID                                                                 
1            3704 N. Western, Oklahoma City, OK 73118  35.507996 -97.529520
2             1503 Winding Ridge Rd, Edmond, OK 73034  35.670379 -97.394095
3           8309 NW 146th St, Oklahoma City, OK 73142  35.620098 -97.662728

In [28]:
# Full outer join to merge location data with coordinates on CustomerID key value
df_customers = pd.merge(df_customers, missing_addresses, on='CustomerID', how='outer')
df_customers = df_customers.drop(['Full Address_y'], axis=1)
df_customers = df_customers.rename(columns={"Full Address_x": "Full Address"})

### Map all historical customers

In [29]:
#generate a folium map to view locations of customers
def generateBaseMap(default_location=[35.507996, -97.529520], default_zoom_start=11):
    base_map = folium.Map(location=default_location,control_scale=True, zoom_start=default_zoom_start)
    return base_map

#create an instance of the map
basemap = generateBaseMap()

# render map
df_customers.apply(lambda row: folium.Circle(location=[row['Latitude'], row['Longitude']],
                                    radius=100, color='Blue', fill_color='Blue').add_to(basemap), axis=1)

basemap

In [30]:
# create new dataframe excluding the first row which is the store's sales, previously
# skewing the binning of TotalSales for customers
sales_colored = df_customers.drop([1])

In [31]:
# count number of customers with $0 in TotalSales
counts = sales_colored[sales_colored['TotalSales'] == 0]
counts.shape

(145, 16)

In [32]:
# new dataframe to plot customers who have > $0 in Total Sales
sales_colored = sales_colored[sales_colored['TotalSales'] > 0]
sales_colored.shape

(2125, 16)

In [33]:
sales_colored['TotalSales'].describe()

count     2125.000000
mean      1745.487007
std       3654.215400
min          0.010000
25%        319.200000
50%        802.000000
75%       1800.000000
max      68884.840000
Name: TotalSales, dtype: float64

In [34]:
# Bin customers by Total Sales using min, Q1, Q3, and max amounts
# new bins to label customers who spend statistically low, med, and high amounts
bins_new = [0, 319, 1800, 10000, 69000]  #min,Q1,Q3,max

In [35]:
# add new bin labels to dataframe
# Red, Yellow, Green, and Purple representing low, medium, high, and extra high spending amounts
sales_colored['marker_color'] = pd.cut(sales_colored['TotalSales'], bins_new, 
                              labels=['Red', 'Yellow', 'Green', 'Purple'], include_lowest=True)
sales_colored[['TotalSales','marker_color']].head()

TotalSales marker_color
CustomerID                         
2               249.50          Red
3              1501.19       Yellow
4              9924.20        Green
5              1533.50       Yellow
6              1048.00       Yellow

### Map customers by spending category with filtering capabilities 

In [36]:
#generate a folium map to view locations of customers
def generateBaseMap(default_location=[35.507996, -97.529520], default_zoom_start=11):
    base_map = folium.Map(location=default_location, tiles='Stamen Toner',control_scale=True, zoom_start=default_zoom_start)
    return base_map

#create a second instance of the map
basemap2 = generateBaseMap()

#dictionary to store colors of FeatureGroup for Layer Control of different customer Total Sales ranges
features = {}
for row in pd.unique(sales_colored["marker_color"]):  #add colors to features
    features[row] = folium.FeatureGroup(name=row)

for index, row in sales_colored.iterrows():
    circ = folium.CircleMarker([row['Latitude'], row['Longitude']], popup=('Total Sales: ${}'.format(row['TotalSales'])),radius=2.5,fill=True, color=row['marker_color'])
    circ.add_to(features[row['marker_color']])

for row in pd.unique(sales_colored["marker_color"]):
    features[row].add_to(basemap2)

folium.LayerControl().add_to(basemap2)

basemap2

In [37]:
# show percentages of customers for each Total Sales category
sales_colored['marker_color'].value_counts(normalize=True)

Yellow    0.500235
Red       0.249882
Green     0.229176
Purple    0.020706
Name: marker_color, dtype: float64

In [38]:
# filters to find customers active within this past year
end_date = '2020-09-01'
start_date = '2020-01-01'
recent_customers = sales_colored[(sales_colored['ActivityDate'] >= start_date) & (sales_colored['ActivityDate'] < end_date)]
recent_customers.head()

Address           City State Postal Code  \
CustomerID                                                          
5               702 Wakefield Rd          Perry    OK       73077   
43             2701 Elmhurst Ave  Oklahoma City    OK       73120   
84          12912 River Oaks Dr.  Oklahoma City    OK       73142   
110             1109 Oak Tree Dr         Edmond    OK       73025   
120             16217 Old Oak Dr         Edmond    OK       73013   

            AccountBalance OpenedDate ActivityDate Street2  ActiveItems  \
CustomerID                                                                
5                     0.00 2015-09-23   2020-06-29     NaN          0.0   
43                    1.57 2015-09-29   2020-02-29     NaN          0.0   
84                  287.73 2015-10-12   2020-08-05     NaN          0.0   
110                   0.00 2015-10-23   2020-03-04     NaN          0.0   
120                   0.00 2015-10-28   2020-07-01     NaN          0.0   

           PickupDate PickupDate2 PickupDate3  TotalSales  \
CustomerID                                                  
5                 NaT         NaT         NaT     1533.50   
43         2016-01-03  2016-12-14  2017-06-07     2438.19   
84         2019-08-12  2019-08-13  2020-08-14    17402.13   
110               NaT         NaT         NaT     4798.53   
120               NaT         NaT         NaT     5283.25   

                                             Full Address   Latitude  \
CustomerID                                                             
5                       702 Wakefield Rd, Perry, OK 73077  36.304138   
43             2701 Elmhurst Ave, Oklahoma City, OK 73120  35.553558   
84          12912 River Oaks Dr., Oklahoma City, OK 73142  35.601172   
110                    1109 Oak Tree Dr, Edmond, OK 73025  35.717694   
120                    16217 Old Oak Dr, Edmond, OK 73013  35.636079   

            Longitude marker_color  
CustomerID                          
5          -97.288293       Yellow  
43         -97.561755        Green  
84         -97.603643       Purple  
110        -97.499466        Green  
120        -97.605394        Green

### Map all customers active within the last year (Jan 1, 2020 to present)

In [39]:
#generate a folium map to view locations of customers
def generateBaseMap(default_location=[35.507996, -97.529520], default_zoom_start=11):
    base_map = folium.Map(location=default_location, tiles='Stamen Toner',control_scale=True, zoom_start=default_zoom_start)
    return base_map

#create a third instance of the map
basemap3 = generateBaseMap()

#dictionary to store colors of FeatureGroup for Layer Control of different customer Total Sales ranges
features = {}
for row in pd.unique(recent_customers["marker_color"]):  #add colors to features
    features[row] = folium.FeatureGroup(name=row)

for index, row in recent_customers.iterrows():
    circ = folium.CircleMarker([row['Latitude'], row['Longitude']], popup=('Total Sales: ${}'.format(row['TotalSales'])),radius=2.5,fill=True, color=row['marker_color'])
    circ.add_to(features[row['marker_color']])

for row in pd.unique(recent_customers["marker_color"]):
    features[row].add_to(basemap3)

folium.LayerControl().add_to(basemap3)

basemap3

In [40]:
# show percentages of customers for each Total Sales category within the past year
recent_customers['marker_color'].value_counts(normalize=True)

Yellow    0.451056
Green     0.282150
Red       0.213052
Purple    0.053743
Name: marker_color, dtype: float64

In [41]:
# add in competitor locations along with original 2 K&N Stores
folium.Marker([35.507996, -97.52952], icon=folium.Icon(color='red'), popup='<i>K&N Store</i>').add_to(basemap2)
folium.Marker([35.612610, -97.552887], icon=folium.Icon(color='red'), popup='<i>Old K&N Store</i>').add_to(basemap2)
folium.Marker([35.566970, -97.566444], icon=folium.Icon(color='red'), popup='<i>Old K&N Store - Interior</i>').add_to(basemap2)
folium.Marker([35.530529, -97.566109], popup='<i>Furniture by Consignment</i>').add_to(basemap2)
folium.Marker([35.627080, -97.507000], popup='<i>2 Doors Down Furniture Consignment</i>').add_to(basemap2)
folium.Marker([35.623380, -97.483550], popup='<i>Furniture by Consignment</i>').add_to(basemap2)
folium.Marker([35.434930, -97.552580], popup='<i>Jimmys Used Furniture</i>').add_to(basemap2)
folium.Marker([35.651820, -97.494920], popup='<i>Elephant Trunk Furniture Consignment</i>').add_to(basemap2)
folium.Marker([35.4781543, -97.5149583], popup='<i>Capps Furniture and Appliances</i>').add_to(basemap2)
folium.Marker([35.464096, -97.58045], popup='<i>Bob Mills</i>').add_to(basemap2)
folium.Marker([35.6098423, -97.5670869], popup='<i>Ashley HomeStore</i>').add_to(basemap2)


basemap2

In [42]:
x = list(sales_colored['ActivityDate'].sort_values())

In [43]:
x[0]

Timestamp('2015-11-02 00:00:00')

In [46]:
# imports
import ipyleaflet
from ipyleaflet import Map
import ipywidgets
from ipyleaflet import basemaps, Map, Marker, FullScreenControl, Circle
from IPython.display import IFrame


In [47]:
# create ipywidgets slider
selection_slider = ipywidgets.SelectionSlider(options=x,
                                              value=x[0],
                                              description='Slider',
                                              disabled=False,
                                              continuous_update=False,
                                              orientation='horizontal',
                                              readout=True)

# create map
customers_history = Map(center=[35.507996, -97.529520], default_zoom_start=3)
customers_history.add_control(FullScreenControl())

# display map
display(customers_history)

# plot customer locations using widget
def plot_customers(date):
    c = sales_colored.loc[sales_colored['ActivityDate'] == date]
    for (index, row) in c.iterrows():
        marker = Circle(location=[row.loc['Latitude'], row.loc['Longitude']], radius=2)
        customers_history.add_layer(marker)
    #print(sales_colored.loc[sales_colored['ActivityDate'] == date])  
ipywidgets.interact(plot_customers, date=selection_slider)

Map(center=[35.507996, -97.52952], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title',…

interactive(children=(SelectionSlider(continuous_update=False, description='Slider', options=(Timestamp('2015-…

<function __main__.plot_customers(date)>